# Restaurant Supply Co. - expansion in NYC

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Analysis Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>


The <b>'Restaurant Supply Co'</b> is a new small company hiring us on Coursera to help them with an ideal location for the first Sales Team in New York City.

<b>The Sales Team</b>, <br>
<b>main requirement</b> is to receive a list of the top Neighborhood with higher density of restaurants in New York City<br>
<b>in such way</b> that the salesmen may be located in the Neighborhood to cover most restaurants with minimum distance. <br>
<br>
<b>secondary requirement </b> <br>
Given that a salesman is able to have 40 restaurants in his portifolio, and the company wants to have 5 salesman at most. <br>
Determine how many clusters and recomend the central location for each one of them<br>
<br>
  


## Data  <a name="data"></a>


For this case, it makes sense to use the <a href=https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json> newyork_data.json </a> data available on Coursera.
<br>    
From newyork_data.json it will be used 'Borough', 'Neighborhood', 'Latitude', 'Longitude', making possible to retrieve venues from <b>Foursquare</b>. From those venues it will be selected/filtered those with one the words: restaurant, bakery, coffee, café, bar, breakfast, burger, creperie, food, gastro, hot dog, pub and steakhouse.
<br><br>
<b>The first deliverable</b> will be ready when data collection and cleanning is completed in the previous step, it means, the complete list of neighborhoods with restaurants quantity.    
<br>
<b>The secondary deliverable</b> will be obtained from the quantity of restaurants in New York City, it will be calculated the quantity of clusters by dividing the restaurants of NY by 40 * 5 (40 restaurants times 5 salesmen per Sales Team Location). With this number, obtain the k-mean and determine the center of each cluster. 
<br><br>


#### from newyork_data.json

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

import wget

#get data file from Cousera and transform in a pandas DataFrame
wget.download('https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json', 'newyork_data.json')
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']    
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
neighborhoods = pd.DataFrame(columns=column_names)
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

100% [............................................................................] 115774 / 115774

#### setup Foursquare credentials

In [2]:
#prepare credentials for Foursquare
CLIENT_ID = 'ALVM5DKWATEHOR43TP2DPVHDMU5CTD2QIV3SWZSU5SKBY0GR' # your Foursquare ID
CLIENT_SECRET = 'PBPMTTVA4UB2KTQOIVZXQRFNZ0WPSA1YKQRG0FJUSNH5HWB1' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value


#### function to iterate neighborhood retrieving Venues in a radius of 500 meters

In [3]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [4]:
#lets use the function above for all neighborhood of NYC
nyc_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                               latitudes=neighborhoods['Latitude'],
                               longitudes=neighborhoods['Longitude']
                              )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

## main deliverable
#### from this list of venues retrieved from Foursquare
1. use the word_set and clean undesired venues
2. attempt to main_deliverable and determine the neighborhood with most restaurants

In [5]:
word_set = set(['restaurant', 'bakery', 'coffee', 'café', 'bar', 'breakfast', 'burger', 'creperie', 'food', 'gastro', 'hot dog', 'pub', 'steakhouse'])
rows_list = []
for i, row in nyc_venues.iterrows():
    category = set(row[6].lower() .split())
    if word_set.intersection(category):    
        rows_list.append(row)
nyc_filtered = pd.DataFrame(rows_list) 

main_deliverable = nyc_filtered.groupby(['Neighborhood']).size().reset_index(name='counts')
main_deliverable = main_deliverable.sort_values(by=['counts'], ascending=False)
#this the list requested by 'Restaurant Supplier Co'
main_deliverable

Neighborhood  counts
170                Murray Hill      88
6                      Astoria      65
255            Upper West Side      63
232                 South Side      61
76                East Village      60
251                 Turtle Bay      57
112          Greenwich Village      55
45                   Chinatown      55
175                       Noho      55
178                 North Side      54
198           Prospect Heights      53
264               West Village      53
68                    Downtown      52
242          Sunnyside Gardens      52
39             Carroll Gardens      50
141               Little Italy      50
160              Midtown South      49
137                 Lenox Hill      49
44                     Chelsea      48
38               Carnegie Hill      47
88          Financial District      47
55                 Cobble Hill      47
48                Civic Center      45
127            Jackson Heights      45
52                     Clinton      45
111                 Greenpoint      44
275                  Yorkville      44
14                     Bayside      44
244               Sutton Place      43
53                Clinton Hill      43
90                    Flatiron      42
21                     Belmont      41
254            Upper East Side      41
106                   Gramercy      39
274                   Woodside      39
249                    Tribeca      39
159                    Midtown      37
228                       Soho      37
113           Hamilton Heights      36
11                   Bay Ridge      36
124              Hunters Point      36
260         Washington Heights      36
35                    Bushwick      35
250                 Tudor City      34
32            Brooklyn Heights      34
97                 Fort Greene      32
25                 Boerum Hill      32
93                    Flushing      31
77           East Williamsburg      31
126                     Inwood      31
189                 Park Slope      31
150             Manhattanville      31
143           Long Island City      30
122               Hudson Yards      29
139             Lincoln Square      27
199  Prospect Lefferts Gardens      26
142                Little Neck      26
105                    Gowanus      25
145            Lower East Side      25
83                    Elmhurst      25
133                Kingsbridge      25
149           Manhattan Valley      24
241                  Sunnyside      24
73                 East Harlem      22
98               Fort Hamilton      22
100               Fulton Ferry      20
214             Rockaway Beach      20
94                     Fordham      20
9                   Bath Beach      20
206                  Rego Park      20
163        Morningside Heights      20
42              Central Harlem      20
69                       Dumbo      19
10           Battery Park City      18
262              West Brighton      18
28              Brighton Beach      18
56               College Point      17
211                  Ridgewood      17
65                 Ditmas Park      17
205                   Red Hook      17
131                Kew Gardens      17
268               Williamsburg      16
258               Vinegar Hill      15
200        Prospect Park South      15
204                 Ravenswood      15
16          Bedford Stuyvesant      15
243                Sunset Park      14
129              Jamaica Hills      14
120                  Homecrest      14
134        Kingsbridge Heights      13
162                 Mill Basin      13
191                 Pelham Bay      13
22                 Bensonhurst      13
34                  Bulls Head      13
80              Edgewater Park      12
121               Howard Beach      12
15                Bedford Park      12
171                   New Dorp      11
64               Cypress Hills      11
225             Sheepshead Bay      11
84                 Eltingville      11
61                      Corona      11
1

## second deliverable
#### determination of clusters
lets consider the fact: 40 restaurants per salesman and 5 salesman per team

In [6]:
nyc_filtered.shape

(4073, 7)

In [7]:
print ('Quantity of teams(clusters) in NYC should be {}'.format(round(4111/(40*5))))

Quantity of teams(clusters) in NYC should be 21


## Machine Learning
#### use k-means to determine cluster of each restaurant and the center of each cluster

In [8]:
# set number of clusters
kclusters = 21
# set latitude and longitude of each restaurant
nyc_grouped_clustering = nyc_filtered.drop(['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude', 'Venue', 'Venue Category'], 1)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_grouped_clustering)
# add clustered labels
nyc_filtered.insert(0, 'Cluster Labels', kmeans.labels_)
# add clustered location
nyc_filtered['Cluster Latitude'] = 0
nyc_filtered['Cluster Longitude'] = 0
for i, row in nyc_filtered.iterrows():
    nyc_filtered.loc[i, 'Cluster Latitude'] = kmeans.cluster_centers_[row['Cluster Labels'], 0]
    nyc_filtered.loc[i, 'Cluster Longitude'] = kmeans.cluster_centers_[row['Cluster Labels'], 1]

#### examining some clusters

In [9]:
nyc_filtered.loc[nyc_filtered['Cluster Labels'] == 0, nyc_filtered.columns[[1] + list(range(5, nyc_filtered.shape[1]))]]

Neighborhood  Venue Latitude  Venue Longitude  \
5843              Woodside       40.746829       -73.896257   
5851              Woodside       40.746070       -73.896083   
5854              Woodside       40.746233       -73.896142   
5865              Woodside       40.746395       -73.896047   
5878              Woodside       40.746187       -73.896591   
5891       Jackson Heights       40.749952       -73.881903   
5892       Jackson Heights       40.749806       -73.883243   
5893       Jackson Heights       40.750134       -73.880227   
5894       Jackson Heights       40.749833       -73.882376   
5895       Jackson Heights       40.750140       -73.881775   
5896       Jackson Heights       40.749507       -73.883323   
5897       Jackson Heights       40.750109       -73.879710   
5898       Jackson Heights       40.749886       -73.882553   
5899       Jackson Heights       40.750018       -73.881291   
5901       Jackson Heights       40.749640       -73.885544   
5904       Jackson Heights       40.755786       -73.883810   
5906       Jackson Heights       40.755705       -73.883145   
5907       Jackson Heights       40.749882       -73.882121   
5908       Jackson Heights       40.749589       -73.885906   
5909       Jackson Heights       40.755731       -73.884203   
5910       Jackson Heights       40.755704       -73.884871   
5912       Jackson Heights       40.755799       -73.885737   
5913       Jackson Heights       40.755465       -73.885675   
5914       Jackson Heights       40.755988       -73.882747   
5915       Jackson Heights       40.750169       -73.880150   
5918       Jackson Heights       40.755999       -73.882393   
5920       Jackson Heights       40.747677       -73.882399   
5921       Jackson Heights       40.747514       -73.882117   
5922       Jackson Heights       40.755388       -73.886429   
5923       Jackson Heights       40.755880       -73.882904   
5924       Jackson Heights       40.749683       -73.882702   
5926       Jackson Heights       40.749498       -73.887387   
5927       Jackson Heights       40.749554       -73.886291   
5929       Jackson Heights       40.756065       -73.881306   
5930       Jackson Heights       40.747992       -73.882145   
5933       Jackson Heights       40.755888       -73.882883   
5934       Jackson Heights       40.749558       -73.887390   
5935       Jackson Heights       40.748220       -73.879639   
5937       Jackson Heights       40.748037       -73.880308   
5939       Jackson Heights       40.749995       -73.880812   
5940       Jackson Heights       40.756176       -73.881176   
5946       Jackson Heights       40.755540       -73.882835   
5947       Jackson Heights       40.755901       -73.882810   
5949       Jackson Heights       40.756045       -73.881647   
5953       Jackson Heights       40.750431       -73.877951   
5956       Jackson Heights       40.755856       -73.880495   
5957       Jackson Heights       40.755737       -73.883982   
5960       Jackson Heights       40.748083       -73.880205   
5961       Jackson Heights       40.755496       -73.884537   
5965       Jackson Heights       40.748263       -73.879485   
5969              Elmhurst       40.743014       -73.883057   
5970              Elmhurst       40.742850       -73.882913   
5972              Elmhurst       40.744701       -73.884615   
5973              Elmhurst       40.741663       -73.882177   
5974              Elmhurst       40.741339       -73.881330   
5975              Elmhurst       40.741226       -73.881261   
5977              Elmhurst       40.741753       -73.878696   
5978              Elmhurst       40.740689       -73.879389   
5979              Elmhurst       40.741078       -73.879996   
5980              Elmhurst       40.741416       -73.880102   
5981              Elmhurst       40.747514       -73.882117   
5982              Elmhurst       40.741614       -73.882115   
5983              Elmhurst       40.746942   

In [10]:
nyc_filtered.loc[nyc_filtered['Cluster Labels'] == 1, nyc_filtered.columns[[1] + list(range(5, nyc_filtered.shape[1]))]]

Neighborhood  Venue Latitude  Venue Longitude  \
3365           Chinatown       40.715135       -73.991802   
3366           Chinatown       40.717010       -73.993530   
3368           Chinatown       40.714476       -73.992036   
3369           Chinatown       40.714704       -73.991847   
3370           Chinatown       40.717278       -73.994177   
3377           Chinatown       40.715232       -73.997263   
3381           Chinatown       40.714459       -73.991546   
3386           Chinatown       40.716735       -73.995752   
3389           Chinatown       40.714830       -73.991719   
3390           Chinatown       40.714713       -73.991538   
3392           Chinatown       40.714880       -73.991175   
3393           Chinatown       40.714763       -73.991455   
3395           Chinatown       40.713654       -73.995192   
3397           Chinatown       40.718291       -73.992584   
3399           Chinatown       40.714468       -73.991589   
3401           Chinatown       40.713618       -73.995978   
3402           Chinatown       40.715661       -73.996693   
3404           Chinatown       40.718145       -73.991988   
3405           Chinatown       40.718254       -73.995930   
3407           Chinatown       40.717560       -73.992580   
3408           Chinatown       40.714470       -73.998018   
3412           Chinatown       40.715720       -73.990332   
3413           Chinatown       40.717824       -73.992801   
3415           Chinatown       40.714317       -73.990361   
3416           Chinatown       40.713974       -73.990868   
3417           Chinatown       40.715876       -73.990467   
3418           Chinatown       40.715004       -73.991010   
3419           Chinatown       40.716360       -73.991356   
3420           Chinatown       40.718366       -73.994490   
3423           Chinatown       40.715787       -73.996905   
3428           Chinatown       40.718215       -73.994345   
3429           Chinatown       40.718145       -73.991978   
3430           Chinatown       40.712349       -73.994295   
3432           Chinatown       40.718057       -73.992060   
3433           Chinatown       40.716765       -73.997874   
3434           Chinatown       40.715976       -73.989862   
3435           Chinatown       40.715520       -73.997973   
3436           Chinatown       40.714639       -73.991013   
3437           Chinatown       40.714452       -73.997991   
3438           Chinatown       40.712968       -73.995149   
3439           Chinatown       40.715039       -73.996941   
3440           Chinatown       40.714198       -73.990157   
3441           Chinatown       40.717722       -73.990497   
3442           Chinatown       40.714368       -73.997869   
3443           Chinatown       40.714512       -73.998235   
3445           Chinatown       40.717690       -73.990435   
3447           Chinatown       40.715545       -73.998137   
3448           Chinatown       40.718316       -73.991885   
3449           Chinatown       40.716196       -73.998303   
3450           Chinatown       40.717847       -73.990358   
3451           Chinatown       40.714695       -73.992672   
3452           Chinatown       40.718432       -73.991701   
3454           Chinatown       40.713992       -73.990169   
3455           Chinatown       40.717450       -73.998373   
3456           Chinatown       40.715069       -73.989952   
4619             Chelsea       40.742539       -74.003812   
4624             Chelsea       40.742120       -74.004612   
4637             Chelsea       40.742598       -74.006078   
4640             Chelsea       40.742000       -74.005890   
4644             Chelsea       40.741662       -74.005080   
4651             Chelsea       40.742729       -74.006438   
4654             Chelsea       40.742085       -74.005594   
4660             Chelsea       40.742384       -74.006456   
4661             Chelsea       40.742074       -74.005012   
4668             Chelsea       40.741865       

In [11]:
nyc_filtered.loc[nyc_filtered['Cluster Labels'] == 15, nyc_filtered.columns[[1] + list(range(5, nyc_filtered.shape[1]))]]

Neighborhood  Venue Latitude  Venue Longitude  \
1303          Gravesend       40.596971       -73.973677   
1304          Gravesend       40.597097       -73.974483   
1306          Gravesend       40.596633       -73.978182   
1307          Gravesend       40.597162       -73.971599   
1312          Gravesend       40.596860       -73.974630   
1314          Gravesend       40.596386       -73.973618   
1316          Gravesend       40.596874       -73.972654   
1320          Gravesend       40.596480       -73.976948   
1326          Gravesend       40.596167       -73.978314   
1327          Gravesend       40.596140       -73.978737   
1332     Brighton Beach       40.576636       -73.967238   
1334     Brighton Beach       40.577245       -73.964573   
1335     Brighton Beach       40.577256       -73.962730   
1338     Brighton Beach       40.576380       -73.965797   
1341     Brighton Beach       40.577851       -73.960968   
1342     Brighton Beach       40.576474       -73.965050   
1343     Brighton Beach       40.577408       -73.961244   
1344     Brighton Beach       40.576609       -73.966667   
1348     Brighton Beach       40.576615       -73.967350   
1353     Brighton Beach       40.575108       -73.961581   
1355     Brighton Beach       40.576992       -73.964870   
1360     Brighton Beach       40.577244       -73.962071   
1361     Brighton Beach       40.574914       -73.962700   
1364     Brighton Beach       40.577841       -73.961204   
1367     Brighton Beach       40.575471       -73.969103   
1368     Brighton Beach       40.574993       -73.962758   
1369     Brighton Beach       40.575997       -73.968887   
1370     Brighton Beach       40.577883       -73.960837   
1374     Sheepshead Bay       40.583842       -73.944481   
1377     Sheepshead Bay       40.583368       -73.941053   
1378     Sheepshead Bay       40.583824       -73.946849   
1379     Sheepshead Bay       40.583371       -73.940841   
1384     Sheepshead Bay       40.583378       -73.939487   
1388     Sheepshead Bay       40.583888       -73.943235   
1392     Sheepshead Bay       40.583739       -73.947066   
1393     Sheepshead Bay       40.588799       -73.947500   
1394     Sheepshead Bay       40.588779       -73.947507   
1396     Sheepshead Bay       40.583790       -73.947231   
1399     Sheepshead Bay       40.590145       -73.939858   
1407  Manhattan Terrace       40.612942       -73.962869   
1414  Manhattan Terrace       40.618227       -73.957961   
1419  Manhattan Terrace       40.618278       -73.957691   
1420  Manhattan Terrace       40.618238       -73.956395   
2377          Flatlands       40.626595       -73.927438   
2389          Flatlands       40.628989       -73.923789   
2395    Manhattan Beach       40.578836       -73.938229   
2400    Manhattan Beach       40.578364       -73.938407   
2408       Coney Island       40.575592       -73.983271   
2411       Coney Island       40.572648       -73.987524   
2490    Gerritsen Beach       40.586655       -73.929179   
2495    Gerritsen Beach       40.592799       -73.925420   
2498    Gerritsen Beach       40.594423       -73.929989   
2499    Gerritsen Beach       40.586918       -73.928955   
2507        Marine Park       40.609311       -73.931668   
2508        Marine Park       40.609023       -73.932480   
2928            Midwood       40.625402       -73.961649   
2999         Georgetown       40.626501       -73.916224   
3002         Georgetown       40.619633       -73.917918   
3003         Georgetown       40.625874       -73.917460   
3004         Georgetown       40.626405       -73.916976   
3006         Georgetown       40.619543       -73.916111   
3014         Georgetown       40.619384       -73.916243   
3019         Georgetown       40.626244       -73.917696   
3021         Georgetown       40.627275       -73.917666   
3287      Ocean Parkway       40.612942       -73.962869   
3294      Ocean Parkway       40.615275       -73.9

## Analysis Results and Discussion <a name="results"></a>

### Main Delivery

<b>Restaurant Supplier Co.</b>, received the list of the neighborhood with most restaurants.<br>
We at Coursera are pointing the 10 neighborhood. That represents 618 of 4111 restaurants in NYC or 15% of the total.
Murray Hill demands 2 salesman to cover the area. 

In [12]:
main_deliverable.head(10)

Neighborhood  counts
170        Murray Hill      88
6              Astoria      65
255    Upper West Side      63
232         South Side      61
76        East Village      60
251         Turtle Bay      57
112  Greenwich Village      55
45           Chinatown      55
175               Noho      55
178         North Side      54

### Secondary Delivery

Actually NYC has 4111 restaurants, which lead us to 21 Sales Teams attending the prerequisites of the instructions.
We have scientifically determined 21 center locations for each of the Sales Teams and respective restaurants for the area of responsibility. 


In [13]:
#get location of NYC
address = 'New York City, NY'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyc_filtered['Cluster Latitude'], nyc_filtered['Cluster Longitude'], nyc_filtered['Cluster Labels'], nyc_filtered['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Conclusion <a name="conclusion"></a>

Purpose of this project was to identify NYC areas high number of restaurants in order to aid stakeholders in narrowing down the search for optimal location for restaurant supplies sales. By calculating restaurant density distribution from Foursquare data we have first identified to 10 Neighbourhoods with Murray Hill at the top with 88 restaurants, and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to balance Sales Team centers, and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.


### Thanks for reading my notebook
Best Regards,<br>
Fabio Nozoy <br>
<a href=“mailto:fnozoy@yahoo.com” target=“_top”>
fnozoy@yahoo.com</a>